# Cast civitai trained LoRa in torch.bfloat16 to Tensor Art Compatible torch.float16 dtype

Created by Adcom: https://tensor.art/u/743241123023077878

In [ ]:
#initialize
import torch
from safetensors.torch import load_file
from google.colab import drive
drive.mount('/content/drive')

In [28]:


device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

doll = load_file('/content/drive/MyDrive/Saved from Chrome/dolls.safetensors')
euro = load_file('/content/drive/MyDrive/Saved from Chrome/euro.safetensors')
scale = load_file('/content/drive/MyDrive/Saved from Chrome/scale.safetensors')
cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi.safetensors')
guns = load_file('/content/drive/MyDrive/Saved from Chrome/guns.safetensors')
iris = load_file('/content/drive/MyDrive/Saved from Chrome/iris.safetensors')

for key in doll:
  doll[f'{key}'] = doll[f'{key}'].to(device = device , dtype=torch.float16)
  euro[f'{key}'] = euro[f'{key}'].to(device = device , dtype=torch.float16)
  scale[f'{key}'] = scale[f'{key}'].to(device = device , dtype=torch.float16)
  iris[f'{key}'] = iris[f'{key}'].to(device = device , dtype=torch.float16)
  cgi[f'{key}'] = cgi[f'{key}'].to(device = device , dtype=torch.float16)
  guns[f'{key}'] = guns[f'{key}'].to(device = device , dtype=torch.float16)

In [10]:
cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi_style.safetensors')

In [57]:
#cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi_style.safetensors')
doll = load_file('/content/drive/MyDrive/Saved from Chrome/dolls.safetensors')
euro = load_file('/content/drive/MyDrive/Saved from Chrome/euro.safetensors')
scale = load_file('/content/drive/MyDrive/Saved from Chrome/scale.safetensors')
cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi.safetensors')
guns = load_file('/content/drive/MyDrive/Saved from Chrome/guns.safetensors')
iris = load_file('/content/drive/MyDrive/Saved from Chrome/iris.safetensors')

In [60]:
for key in doll:
  doll[f'{key}'] = doll[f'{key}'].to(dtype=torch.float16)
  euro[f'{key}'] = euro[f'{key}'].to(dtype=torch.float16)
  scale[f'{key}'] = scale[f'{key}'].to(dtype=torch.float16)

In [104]:
import torch
import torch.nn as nn
#define metric for similarity
tgt_dim = torch.Size([64, 3072])
cos0 = nn.CosineSimilarity(dim=1)
cos = nn.CosineSimilarity(dim=1)


def sim(tgt , ref ,key):
  return torch.sum(torch.abs(cos(tgt, ref[f'{key}'])))  + torch.sum(torch.abs(cos0(tgt, ref[f'{key}'])))
#-----#

from torch import linalg as LA

LA.matrix_norm
def rand_search(A , B , key , iters):
  tgt_norm = (LA.matrix_norm(A[f'{key}']) + LA.matrix_norm(B[f'{key}']))/2
  tgt_avg = (A[f'{key}'] + B[f'{key}'])/2

  max_sim = (sim(tgt_avg , A , key) + sim(tgt_avg , B , key))
  cand = tgt_avg

  for iter in range(iters):
    rand = torch.ones(tgt_dim)*(-0.5)  + torch.rand(tgt_dim)
    rand = rand  * (tgt_norm/LA.matrix_norm(rand))
    #rand = (rand + tgt_avg)/2
    #rand = rand  * (tgt_norm/LA.matrix_norm(rand))

    tmp = sim(rand,A, key) + sim(rand , B, key)
    if (tmp > max_sim):
      max_sim = tmp
      cand = rand
      print('found!')
      break
  #------#
  print('returning')
  return cand  , max_sim
#-----#

In [106]:
cand , max_sim = rand_search(cgi , iris , 'lora_unet_double_blocks_0_img_attn_proj.lora_down.weight' , 1000)
print(sim(cand , iris , key))
print(sim(cand , cgi , key))

returning
tensor(91.1875, dtype=torch.float16)
tensor(90.2500, dtype=torch.float16)


In [16]:
(torch.rand(1).to(dtype=torch.float16)*3).item()

0.2138671875

In [13]:
torch.rand(1).to(dtype=torch.float16)*10

tensor([6.8555], dtype=torch.float16)

In [37]:
import torch
import torch.nn as nn
#define metric for similarity
tgt_dim = torch.Size([64, 3072])
cos0 = nn.CosineSimilarity(dim=0)



cos = nn.CosineSimilarity(dim=1)


def sim(tgt , ref ,key):
  return torch.sum(torch.abs(cos(tgt, ref[f'{key}'])))  + torch.sum(torch.abs(cos0(tgt, ref[f'{key}'])))
#-----#

7.715576171875

In [33]:
from safetensors.torch import load_file , save_file
import torch
import torch.nn as nn
from torch import linalg as LA
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#define metric for similarity
cos0 = nn.CosineSimilarity(dim=0).to(device)
final_score = 0
highest_score = 0
w_cgi = 1
w_doll = 2
w_euro = 2
w_guns = 1
w_iris = 2
w_scale = 1

w_noise = 0.00001 * (w_cgi + w_doll + w_euro  + w_guns + w_iris + w_scale)
fixed_noise = {}

#for key in doll:
#  fixed_noise[f'{key}'] = torch.zeros(doll[f'{key}'].shape).to(device = device , dtype=torch.float16)
#------#
#w_offset = 0* (w1+w2+w3)
#_w_offset = 0

W =  (w_cgi + w_doll + w_euro  + w_guns + w_iris + w_scale + w_noise)*torch.ones(1).to(device = device,dtype=torch.float16)

SCALE = 0.0001
one = torch.ones(1).to(dtype=torch.float16).to(device)

for attempt in range(1000):
  print(f'attempt no : {attempt+1} ')
  merge = load_file('/content/drive/MyDrive/Saved from Chrome/dolls.safetensors')
  for key in doll:
    tgt_dim = doll[f'{key}'].shape
    if tgt_dim == torch.Size([]): continue
    r_cgi = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_cgi
    r_doll = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_doll
    r_euro = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_euro
    r_guns = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_guns
    r_iris = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_iris
    r_scale = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_scale
    #------#
    noise = torch.rand(tgt_dim).to(device = device,dtype=torch.float16)
    noise_norm = LA.matrix_norm(noise).to(device = device,dtype=torch.float16).item()
    noise = (w_noise/noise_norm)*noise.to(device = device,dtype=torch.float16)
    #-----#
    merge[f'{key}'] = r_cgi * cgi[f'{key}'] #overwrite
    merge[f'{key}'] = merge[f'{key}'] + r_doll * doll[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_euro * euro[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_guns * guns[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_iris * iris[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_scale * scale[f'{key}']
    merge[f'{key}'] = ((merge[f'{key}'] + noise)/W).to(device = device,dtype=torch.float16)
  #-------#
  score = torch.zeros(1).to(device = device, dtype=torch.float32)
  #----#
  NUM_ITERS = 10
  for iter in range(NUM_ITERS):
    for key in doll:
      tgt_dim = doll[f'{key}'].shape
      if tgt_dim == torch.Size([]): continue
      vec = torch.rand(tgt_dim[0]).to(device = device,dtype=torch.float16)
      cgi_out = torch.matmul(vec , cgi[f'{key}']).to(device = device,dtype=torch.float16)
      doll_out = torch.matmul(vec , doll[f'{key}']).to(device = device,dtype=torch.float16)
      euro_out = torch.matmul(vec , euro[f'{key}']).to(device = device,dtype=torch.float16)
      guns_out = torch.matmul(vec , guns[f'{key}']).to(device = device,dtype=torch.float16)
      iris_out = torch.matmul(vec , iris[f'{key}']).to(device = device,dtype=torch.float16)
      scale_out = torch.matmul(vec , scale[f'{key}']).to(device = device,dtype=torch.float16)
      merge_out = torch.matmul(vec , merge[f'{key}']).to(device = device,dtype=torch.float16)
      #-------#
      sim_value_cgi = torch.abs(cos0(cgi_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_doll = torch.abs(cos0(doll_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_euro = torch.abs(cos0(euro_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_guns = torch.abs(cos0(guns_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_iris = torch.abs(cos0(iris_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_scale = torch.abs(cos0(scale_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      score = score  + SCALE*(sim_value_cgi + 2*sim_value_doll +  2*sim_value_euro + sim_value_guns + 2*sim_value_iris + sim_value_scale)/9  #<--- This score can be anything at all
      #----#
  #-----#

  final_score = (1000/(NUM_ITERS * SCALE))*score.to(device = 'cpu' , dtype=torch.float32).item()
  if (final_score>highest_score) :
    highest_score = final_score
    print('new highscore!')
    print(f'score : {final_score} pts')
    #------#
    save_file(merge , 'all_merge_R4.safetensors')
  #------#

print(f'------------')
print(f'Final score : {highest_score} pts')


#all R1 23.190992578747682

#all R2 23.333244826062582

#all R3 23.34471355425194

#all R4 23.402637452818453

attempt no : 1 
new highscore!
score : 23.264414267032407 pts
attempt no : 2 
attempt no : 3 
attempt no : 4 
new highscore!
score : 23.29399467271287 pts
attempt no : 5 
attempt no : 6 
attempt no : 7 
attempt no : 8 
attempt no : 9 
attempt no : 10 
attempt no : 11 
new highscore!
score : 23.362628780887462 pts
attempt no : 12 
attempt no : 13 
attempt no : 14 
attempt no : 15 
attempt no : 16 
attempt no : 17 
attempt no : 18 
attempt no : 19 
attempt no : 20 
attempt no : 21 
attempt no : 22 
attempt no : 23 
new highscore!
score : 23.37011210329365 pts
attempt no : 24 
attempt no : 25 
attempt no : 26 
attempt no : 27 
attempt no : 28 
attempt no : 29 
attempt no : 30 
attempt no : 31 
attempt no : 32 
attempt no : 33 
attempt no : 34 
new highscore!
score : 23.402637452818453 pts
attempt no : 35 
attempt no : 36 
attempt no : 37 
attempt no : 38 
attempt no : 39 
attempt no : 40 
attempt no : 41 
attempt no : 42 
attempt no : 43 
attempt no : 44 
attempt no : 45 
attempt no : 46 

KeyboardInterrupt: 

In [ ]:
    for key in doll:
      if final_score<38.5: break
      _w_offset = w_offset
      W =  (w1+w2+w3 + w_noise + _w_offset)*torch.ones(1).to(device = device,dtype=torch.float16)
      tgt_dim = doll[f'{key}'].shape
      if tgt_dim == torch.Size([]): continue
      fixed_noise[f'{key}'] = fixed_noise[f'{key}'] + merge[f'{key}']
      fixed_noise[f'{key}'] = (fixed_noise[f'{key}'] * (w_offset*torch.ones(1).to(device = device,dtype=torch.float16)/LA.matrix_norm(fixed_noise[f'{key}']))).to(device = device,dtype=torch.float16)

In [64]:
  vec = torch.rand(tgt_dim[0]).to(dtype=torch.float16)
  same = torch.abs(cos0(vec ,vec))

In [65]:
same

tensor(1., dtype=torch.float16)

In [66]:
torch.ones(1).to(dtype=torch.float16)

tensor([1.], dtype=torch.float16)

score : 45.8125 pts


In [ ]:
%cd /content/
save_file(merge , 'doll_euro_scale_R_merge.safetensors')

In [47]:
test = torch.rand(tgt_dim)
vec = torch.rand(tgt_dim[0])

In [46]:
tgt_dim[0]

9216

In [48]:
(torch.matmul(vec,test)).shape

torch.Size([64])

In [39]:
tgt_dim = torch.Size([64, 3072])
cosa = nn.CosineSimilarity(dim=0)
cos_dim1 = nn.CosineSimilarity(dim=1)

for key in cgi:
  if not cgi[f'{key}'].shape == torch.Size([64, 3072]): continue
  print(f'{key} : ')
  print(torch.sum(torch.abs(cos_dim1(cgi[f'{key}'] , iris[f'{key}']))))

lora_unet_double_blocks_0_img_attn_proj.lora_down.weight : 
tensor(1.6982, dtype=torch.float16)
lora_unet_double_blocks_0_img_attn_qkv.lora_down.weight : 
tensor(1.8145, dtype=torch.float16)
lora_unet_double_blocks_0_img_mlp_0.lora_down.weight : 
tensor(1.6309, dtype=torch.float16)
lora_unet_double_blocks_0_img_mod_lin.lora_down.weight : 
tensor(2.6211, dtype=torch.float16)
lora_unet_double_blocks_0_txt_attn_proj.lora_down.weight : 
tensor(2.3203, dtype=torch.float16)
lora_unet_double_blocks_0_txt_attn_qkv.lora_down.weight : 
tensor(2.3027, dtype=torch.float16)
lora_unet_double_blocks_0_txt_mlp_0.lora_down.weight : 
tensor(2.5898, dtype=torch.float16)
lora_unet_double_blocks_0_txt_mod_lin.lora_down.weight : 
tensor(2.7402, dtype=torch.float16)
lora_unet_double_blocks_10_img_attn_proj.lora_down.weight : 
tensor(2.0410, dtype=torch.float16)
lora_unet_double_blocks_10_img_attn_qkv.lora_down.weight : 
tensor(1.3350, dtype=torch.float16)
lora_unet_double_blocks_10_img_mlp_0.lora_down.weight

<---- Upload your civiai trained .safetensor file to Google Colab before running the next cell



In [ ]:
civiai_lora = '' # @param {type:'string' ,placeholder:'ex. civitai_trained_e19.safetensors'}
tensor_art_filename = '' # @param {type:'string' ,placeholder:'ex. e19.safetensors'}
%cd /content/
tgt = load_file(f'{civiai_lora}')
for key in tgt:
  tgt[f'{key}'] = tgt[f'{key}'].to(dtype=torch.float16)
%cd /content/
save_file(tgt , f'{tensor_art_filename}')

Download the new .safetensor file to your device.

Downloading from CoLab Notebook will seemingly do nothing for ~5min. Then the file will download , so be patient.

For faster/more consistent downloads , download your .safetensor file from your Google Drive